<center><b><font size='10'><font color='78aa58'>G</font><font color='6589bf'>V</font>HMR</font></b></center>

<center><b><font size='5'> World-Grounded Human Motion Recovery via <font color='78aa58'>Gravity</font>-<font color='6589bf'>View</font> <font color='c68b5b'>Coordinates</font></font></b></center>

![](https://zju3dv.github.io/gvhmr/img/teaser_v1.png)


<center><b>
<a href=https://zju3dv.github.io/gvhmr>Project Page</a>
|
<a href=https://arxiv.org/abs/2409.06662>Paper</a>
</b></center>

> World-Grounded Human Motion Recovery via Gravity-View Coordinates  
> [Zehong Shen](https://zehongs.github.io/)<sup>\*</sup>,
[Huaijin Pi](https://phj128.github.io/)<sup>\*</sup>,
[Yan Xia](https://isshikihugh.github.io/scholar),
[Zhi Cen](https://scholar.google.com/citations?user=Xyy-uFMAAAAJ),
[Sida Peng](https://pengsida.net/)<sup>†</sup>,
[Zechen Hu](https://zju3dv.github.io/gvhmr),
[Hujun Bao](http://www.cad.zju.edu.cn/home/bao/),
[Ruizhen Hu](https://csse.szu.edu.cn/staff/ruizhenhu/),
[Xiaowei Zhou](https://xzhou.me/)  
> SIGGRAPH Asia 2024


## Installation

Check [INSTALL.md](https://github.com/IsshikiHugh/GVHMR/blob/main/docs/INSTALL.md) if you want to install GVHMR in your own machine.

> Tips: you can fold the section and run the whole installation section at once.

In [1]:
# Controlling notebook is connected to NVIDIA drivers with CUDA. If this doesn't load check that GPU is selected as hardware accelerator under Edit -> Notebook settings.
# Google may shut down the GPU if usage has surpassed the allocation

!nvidia-smi

Sat Sep 14 17:16:45 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   52C    P8               9W /  70W |      0MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

### Environment Prepration ~ 15 min

Check [INSTALL.md#Environment](https://github.com/IsshikiHugh/GVHMR/blob/main/docs/INSTALL.md#environment) for further information.

In [ ]:
import os
from pathlib import Path

# Clone the repo.
!git clone https://github.com/zju3dv/GVHMR --recursive
proj_root = str(Path('GVHMR').absolute())

# Install GVHMR. (If Colab asks you to restart, just click cancel and rerun the block.)
%cd {proj_root}
%pip install -r requirements.txt
%pip install -e .

In [ ]:
# Install DPVO.
%cd third-party/DPVO

!wget https://gitlab.com/libeigen/eigen/-/archive/3.4.0/eigen-3.4.0.zip
!unzip -o eigen-3.4.0.zip -d thirdparty && rm -rf eigen-3.4.0.zip

%pip install torch-scatter -f "https://data.pyg.org/whl/torch-2.3.0+cu121.html"
%pip install numba pypose

if 'cuda_home' not in locals():
  cuda_home = '/usr/local/cuda-12'
  if not Path(cuda_home).exists():
    raise FileNotFoundError('CUDA_HOME for cuda 12.x not found!')

  os.environ['CUDA_HOME'] = cuda_home
  os.environ['PATH'] = os.environ['PATH'] + f':{cuda_home}/bin'

%pip install -e .
%cd {proj_root}

### Data Prepration ~ 1 min

Check [INSTALL.md#Inputs&Outputs](https://github.com/IsshikiHugh/GVHMR/blob/main/docs/INSTALL.md#inputs--outputs) for further information.

In [11]:
%cd {proj_root}
!mkdir inputs
!mkdir outputs

!apt install -y -qq aria2
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/SMPLer-X/resolve/main/SMPL_NEUTRAL.pkl -d inputs/checkpoints/body_models/smpl -o SMPL_NEUTRAL.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/SMPLer-X/resolve/main/SMPLX_NEUTRAL.npz -d inputs/checkpoints/body_models/smplx -o SMPLX_NEUTRAL.npz
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/GVHMR/resolve/main/dpvo/dpvo.pth -d inputs/checkpoints/dpvo -o dpvo.pth
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/GVHMR/resolve/main/gvhmr/gvhmr_siga24_release.ckpt -d inputs/checkpoints/gvhmr -o gvhmr_siga24_release.ckpt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/GVHMR/resolve/main/hmr2/epoch%3D10-step%3D25000.ckpt -d inputs/checkpoints/hmr2 -o epoch=10-step=25000.ckpt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/GVHMR/resolve/main/vitpose/vitpose-h-multi-coco.pth -d inputs/checkpoints/vitpose -o vitpose-h-multi-coco.pth
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/GVHMR/resolve/main/yolo/yolov8x.pt -d inputs/checkpoints/yolo -o yolov8x.pt

/content/GVHMR
mkdir: cannot create directory ‘inputs’: File exists
mkdir: cannot create directory ‘outputs’: File exists
aria2 is already the newest version (1.36.0-1).
0 upgraded, 0 newly installed, 0 to remove and 49 not upgraded.

Download Results:
gid   |stat|avg speed  |path/URI
======+====+===========+=======================================================
858436|OK  |       0B/s|inputs/checkpoints/body_models/smpl/SMPL_NEUTRAL.pkl

Status Legend:
(OK):download completed.

Download Results:
gid   |stat|avg speed  |path/URI
======+====+===========+=======================================================
da93ed|OK  |       0B/s|inputs/checkpoints/body_models/smplx/SMPLX_NEUTRAL.npz

Status Legend:
(OK):download completed.

Download Results:
gid   |stat|avg speed  |path/URI
======+====+===========+=======================================================
b2dfd7|OK  |       0B/s|inputs/checkpoints/dpvo/dpvo.pth

Status Legend:
(OK):download completed.

Download Results:
gid   |stat|avg

## Run Demo

Use `-s` to skip visual odometry <b><u>if you know the camera is static</u></b>, otherwise the camera will be estimated by DPVO.

We also provide a script demo_folder.py to inference a entire folder.


```shell
python tools/demo/demo.py --video=docs/example_video/tennis.mp4 -s
python tools/demo/demo_folder.py -f inputs/demo/folder_in -d outputs/demo/folder_out -s

```

In [35]:
import io
import base64
from IPython.display import HTML
from hmr4d.utils.video_io_utils import get_video_lwh

def display_video(fn):
    L, W, H = get_video_lwh(fn)
    scale = min(W, 1080) / W
    W, H = int(W * scale), int(H * scale)
    video_encoded = base64.b64encode(io.open(fn, 'rb').read())
    return HTML(data='''<video width="{0}" height="{1}" alt="test" controls>
                        <source src="data:video/mp4;base64,{2}" type="video/mp4" />
                        </video>'''.format(W, H, video_encoded.decode('ascii')))

### Demo Tennis

In [12]:
# Run demo.
video_fn = f'{proj_root}/docs/example_video/tennis.mp4'
!python {proj_root}/tools/demo/demo.py --video={video_fn} -s

[09/14 17:37:05][INFO] [Input]: /content/GVHMR/docs/example_video/tennis.mp4
[09/14 17:37:05][INFO] (L, W, H) = (312, 812, 720)
[09/14 17:37:06][INFO] [Output Dir]: outputs/demo/tennis
[09/14 17:37:06][INFO] [Copy Video] /content/GVHMR/docs/example_video/tennis.mp4 -> outputs/demo/tennis/0_input_video.mp4
Copy: 100% 312/312 [00:09<00:00, 33.08it/s]
[09/14 17:37:17][INFO] [GPU]: Tesla T4
[09/14 17:37:17][INFO] [GPU]: _CudaDeviceProperties(name='Tesla T4', major=7, minor=5, total_memory=15102MB, multi_processor_count=40)
[09/14 17:37:17][INFO] [Preprocess] Start!
YoloV8 Tracking: 100% 312/312 [00:27<00:00, 11.14it/s]
ViTPose: 100% 20/20 [00:42<00:00,  2.13s/it]
HMR2 Feature: 100% 20/20 [00:22<00:00,  1.11s/it]
[09/14 17:39:36][INFO] [Preprocess] End. Time elapsed: 139.28s
[09/14 17:39:36][INFO] [HMR4D] Predicting
[09/14 17:39:36][INFO] [EnDecoder] Use MM_V1_AMASS_LOCAL_BEDLAM_CAM for statistics!
[09/14 17:39:38][INFO] [PL-Trainer] Loading ckpt type: inputs/checkpoints/gvhmr/gvhmr_siga24_

In [36]:
# Visualize the result.
display_video('outputs/demo/tennis/tennis_3_incam_global_horiz.mp4')

### Custom Demo

In order to run your own video, you need to follow instructions below:

0. Run the code block below to initialize `demo_google_drive_video()`.
1. Upload your video on Google drive and set accessbility as "Anyone with link (Viewer)".
2. Copy the link and extract the ID. The link should follow this pattern: `https://drive.google.com/file/d/<Google Drive ID>/view?usp=sharing`.
3. Call `demo_google_drive_video()` with the URL, and pass `True` if the camera is static.


In [31]:
%cd {proj_root}
!mkdir -p inputs/demo

def demo_google_drive_video(url:str, static_camera:bool):
    ''' URL should be like https://drive.google.com/file/d/xxxxxxxx/view?usp=drive_link '''

    print(f'[1/3] 📥 Downloading video...')
    gdid = url.split('/')[5]
    video_name = f'custom_{gdid}'
    download_url = f'\'https://drive.google.com/uc?id={gdid}&export=download&confirm=t\''
    !gdown {download_url} -O inputs/demo/{video_name}.mp4

    print(f'[2/3] 💃 Start running GVHMR...')
    flag = '-s' if static_camera else ''
    !python {proj_root}/tools/demo/demo.py --video=inputs/demo/{video_name}.mp4 {flag}

    print(f'[3/3] 📺 Displaying result...')
    return display_video(f'outputs/demo/{video_name}/{video_name}_3_incam_global_horiz.mp4')

/content/GVHMR


In [39]:
demo_google_drive_video(url='https://drive.google.com/file/d/1KkTsoAuj9yq5JCJ-qg4_MnNBn56wR47F/view?usp=drive_link', static_camera=True)

[1/3] 📥 Downloading video...
Downloading...
From: https://drive.google.com/uc?id=1KkTsoAuj9yq5JCJ-qg4_MnNBn56wR47F&export=download&confirm=t
To: /content/GVHMR/inputs/demo/custom_1KkTsoAuj9yq5JCJ-qg4_MnNBn56wR47F.mp4
100% 936k/936k [00:00<00:00, 9.14MB/s]
[2/3] 💃 Start running GVHMR...
[09/14 18:09:12][INFO] [Input]: inputs/demo/custom_1KkTsoAuj9yq5JCJ-qg4_MnNBn56wR47F.mp4
[09/14 18:09:12][INFO] (L, W, H) = (367, 682, 666)
[09/14 18:09:13][INFO] [Output Dir]: outputs/demo/custom_1KkTsoAuj9yq5JCJ-qg4_MnNBn56wR47F
[09/14 18:09:13][INFO] [Copy Video] inputs/demo/custom_1KkTsoAuj9yq5JCJ-qg4_MnNBn56wR47F.mp4 -> outputs/demo/custom_1KkTsoAuj9yq5JCJ-qg4_MnNBn56wR47F/0_input_video.mp4
Copy: 100% 367/367 [00:09<00:00, 39.06it/s]
[09/14 18:09:23][INFO] [GPU]: Tesla T4
[09/14 18:09:23][INFO] [GPU]: _CudaDeviceProperties(name='Tesla T4', major=7, minor=5, total_memory=15102MB, multi_processor_count=40)
[09/14 18:09:23][INFO] [Preprocess] Start!
YoloV8 Tracking: 100% 367/367 [00:29<00:00, 12.65it/s

In [ ]:
# Try it yourself!
demo_google_drive_video(...)